In [1]:

import time
import gymnasium
from miniwob.action import ActionTypes
from dom_processing import iterate_dom, dict2html, prepare_t5_input
from inference_points import infer_remote_model, parse_t5_output_action
from cc_net5_tokenizer import CCNeT5Tokenizer
from cosine_similarity import find_closest_embeddings
import torch
import numpy as np
import json


/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob/bisect-angle-v1 already in registry.
  logger.warn(f"Overriding environment {new_spec.id} already in registry.")
/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob/book-flight-v1 already in registry.
  logger.warn(f"Overriding environment {new_spec.id} already in registry.")
/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob/book-flight-nodelay-v1 already in registry.
  logger.warn(f"Overriding environment {new_spec.id} already in registry.")
/Library/Frameworks/Python.framework/Versions/3.9/lib/python3.9/site-packages/gymnasium/envs/registration.py:521: UserWarning: WARN: Overriding environment miniwob

In [18]:

def convert_to_nested_dict(elements):
    # Create a dictionary to store elements by their 'ref' value
    element_dict = {element['ref']: element for element in elements}

    # Iterate through the elements to build the nested structure
    for element in elements:
        parent_ref = element['parent']
        if parent_ref != 0:
            parent_element = element_dict.get(parent_ref)
            if 'children' not in parent_element:
                parent_element['children'] = []
            if 'children' not in element:
                # Empty children field
                element['children'] = []
            parent_element['children'].append(element)

    # Find the root element (element with 'parent' = 0)
    root_element = None
    for element in elements:
        if element['parent'] == 0:
            root_element = element
            break

    return root_element

# format image (3, 210, 160) for request by normalizing it
def format_image(image):
    rgb_data = np.transpose(np.array(image) / 255.0, (2, 0, 1))
    return rgb_data

def format_language_rgb_input(rgb_data, dom_data, utterance_data, task_data):
    # Put language task together
    language_input = np.concatenate((dom_data, utterance_data, task_data))
    #language_input = dom_data
    print(language_input.shape)

    rgb_data = torch.from_numpy(rgb_data).type(torch.float32)
    language_input = torch.from_numpy(language_input).type(torch.long)
    language_input = tokenizer.embedding_fn(language_input) # Create embeddings for language
    print(f'rgb_data: {rgb_data.shape}, language_input: {language_input.shape}')
    return rgb_data, language_input

import json

def prepare_ccnet5_payload(rgb_data, language_input, previous_action, t5_output_tensor):
    cc_net5_payload = {
        'rgb_input': rgb_data,
        'language_input': language_input,
        'previous_action': previous_action,
        't5_output': t5_output_tensor,
    }

    cc_net5_payload_numpy = {
        key: value.detach().numpy().tolist() if isinstance(value, torch.Tensor) else value
        for key, value in cc_net5_payload.items()
    }

    json_data = json.dumps(cc_net5_payload_numpy)
    return json_data


# Update the mapping dictionary of ref with page changes
def update_ref2_random(old_dict, old_rand2ref, new_dict):
    _remvoved_refs_keys = old_dict.keys() - new_dict.keys()
    added_refs_keys = new_dict.keys() - old_dict.keys() # no use of old refs, better to keep them in old_dict

    # create subset_dictionary
    added_refs = {}
    for added_ref in added_refs_keys:
        if added_ref in old_dict.keys():
            added_refs[added_ref] = old_dict[added_ref]
        else:
            added_refs[added_ref] = new_dict[added_ref]

    # attribute random to new refs:
    added_refs_dict, added_rand2refs = randomize_ref_dict(list(added_refs.keys()))

    # Update the old dictionary with the new mapping
    old_dict.update(added_refs_dict)
    old_rand2ref.update(added_rand2refs)

    # These are the new mappings
    return old_dict, old_rand2ref

import random

# find all refs of the dom dict
def find_all_refs(dom):
    refs = []
    if 'ref' in dom.keys():
        refs.append(dom['ref'])
    if 'children' in dom.keys():
        for child in dom['children']:
            f_ref = find_all_refs(child)
            refs += f_ref
    return list(set(refs))

# provide ref list and return dictionary with randomized values
# also return dict to reconstruct it all
def randomize_ref_dict(refs):
    entries = refs.copy()
    random.shuffle(entries)
    ref_dict = {}
    for i, k in enumerate(refs):
        ref_dict[k] = entries[i]

    ref2rand = ref_dict
    rand2ref = {}
    for k in ref2rand.keys():
        rand2ref[ref2rand[k]] = k
    return ref_dict, rand2ref

# Assigns the randomized value to each ref of the dom dict
def attribute_random_refs_dom(dom, refs):
    if 'ref' in dom.keys():
        dom['ref'] = refs[dom['ref']]
    if 'children' in dom.keys():
        new_children = []
        for child in dom['children']:
            new_child = attribute_random_refs_dom(child, refs)
            new_children.append(new_child)
        dom['children'] = new_children
    return dom

def call_T5(action_history, utterance, dom):
    html_str = dict2html(dom)
    t5_input = prepare_t5_input(action_history, utterance, html_str)
    print(f't5_input: {t5_input}')
    t5_output = infer_remote_model(t5_input, t5_url)
    t5_action, t5_ref, t5_keydown = parse_t5_output_action(t5_output)
    print(f't5_action: {t5_action}, t5_ref: {t5_ref}, t5_keydown: {t5_keydown}')

    return t5_action, t5_ref, t5_keydown

def call_ccnet5(screenshot, new_dom, previous_action, t5_output_tensor, utterance):
    # format RGB input
  rgb_input = format_image(screenshot)

  # format language input
  tokenized_dom = tokenizer.tokenize_dom(new_dom)
  tokenized_dom = np.array(tokenizer.truncate_pad_entry(tokenized_dom, 492)) # 492 is the value set for CC-NeT5 processing
  tokenized_utterance = np.array(tokenizer.truncate_pad_entry(tokenizer.tokenize_string(utterance), 16))
  tokenized_task_name = np.array(tokenizer.truncate_pad_entry(tokenizer.tokenize_string(task_name), 4))
  rgb_data, language_input = format_language_rgb_input(rgb_input, tokenized_dom, tokenized_utterance, tokenized_task_name)
  # Unsqueeze with batch size to add first dimension
  rgb_data = rgb_data.unsqueeze(0)
  language_input = language_input.unsqueeze(0)

  # format previous action (flattened tensor size 577)
  previous_action = previous_action.unsqueeze(0)
  t5_output_tensor = t5_output_tensor.unsqueeze(0)

  # Inference to model CC-NeT5
  ccnet5_payload = prepare_ccnet5_payload(rgb_data, language_input, previous_action, t5_output_tensor)
  ccnet5_output = infer_remote_model(ccnet5_payload, cc_net5_url)
  ccnet5_action, ccnet5_ref, ccnet5_keydown = parse_t5_output_action(ccnet5_output)

  return ccnet5_action, ccnet5_ref, ccnet5_keydown

In [22]:
# Prepare our Embedding Function
embedding_fn_path = '/Users/lucas-andreithil/PycharmProjects/miniwob-plusplus/embedding_weights.pth'
vocab_path="vocab.txt"
tokenizer = CCNeT5Tokenizer(vocab_path=vocab_path, embedding_fn_path=embedding_fn_path)

t5_url = 'https://a472-35-184-106-71.ngrok-free.app'
cc_net5_url = 'https://324e-34-141-132-209.ngrok-free.app'

pad: 1591
Loaded CC_NeT5 Tokenizer with vocabulary size being 1592.


In [23]:
# Define processing steps of a time step for the agent.
# Returns an action, and ref dictionaries over the steps.
# Pass ref dict of previous actions, empty for first step.
def observe_and_act(observation, ref_dict, rand2ref, action_history):
    # 1: Reformat Screenshot Shape
    screenshot = observation['screenshot']
    print(f'screenshot shape: {screenshot.shape}')

    # 2: Check Utterance
    utterance = observation['utterance']

    # 3: Process DOM
    # convert elements to nested dict structure
    nested_dict = convert_to_nested_dict(observation['dom_elements'])
    # clean
    _, _, new_dom = iterate_dom(nested_dict)
    # randomize references
    ref_dict_new, _rand2ref_new = randomize_ref_dict(find_all_refs(new_dom))
    # update previous dictionaries with new observations
    ref_dict, rand2ref = update_ref2_random(ref_dict, rand2ref, ref_dict_new)
    # apply randomized references to observation DOM
    doms = attribute_random_refs_dom(new_dom, ref_dict)

    # 4: Model call
    # a. T5 call
    # - Format for T5 call
    t5_action, t5_ref, t5_keydown = call_T5(action_history, utterance, doms)
    # format tensor T5_output into Embeddings (flattened tensor) to feed CC-NeT5
    t5_output_tensor = torch.zeros(577)
    if t5_action == 'keydown':
        t5_output_tensor[0:1] = 1
    #t_ref = torch.from_numpy(np.array(tokenizer.truncate_pad_entry(tokenizer.tokenize_string(t5_ref), 64)))
    t_ref = torch.flatten(tokenizer.embedding_fn(torch.from_numpy(np.array(tokenizer.stoi[str(t5_ref)])))).detach()
    t_keydown = torch.flatten(tokenizer.embedding_fn(torch.from_numpy(np.array(tokenizer.truncate_pad_entry(tokenizer.tokenize_string(str(t5_keydown)), 8))))).detach()
    t5_output_tensor[1:65] = t_ref
    t5_output_tensor[65:577] = t_keydown

    # b. CC-NeT5
    ccnet5_action, ccnet5_ref, ccnet5_keydown = call_ccnet5(screenshot, new_dom, previous_action, t5_output_tensor, utterance)

    if ccnet5_action == 'click':
        action_type = ActionTypes.CLICK_ELEMENT
    else:
        action_type = ActionTypes.TYPE_TEXT

    # Sample and Create Action
    action = env.action_space.sample()     # Template for the action.
    action["action_type"] = env.action_space_config.action_types.index(
      action_type
    )
    # Get the ref number by using the dictionary mapping random to old reference
    action["ref"] = str(rand2ref[ccnet5_ref])
    # Add text if action is type_text
    if action_type == ActionTypes.TYPE_TEXT:
        action['text'] = ccnet5_keydown

    return action, ref_dict, rand2ref

In [24]:
task_name = 'click-test-2-v1'
#task_name = 'click-checkboxes-transfer'
env = gymnasium.make(f"miniwob/{task_name}")

In [27]:
# Episode Data
dom_episode = []
action_history = []
# Set up previous_action with default values
previous_action = torch.zeros(577)

# Empty ref dictionaries at start of episode:
ref_dict, rand2ref = {}, {}
observation, info = env.reset()

for i in range(3):
    print(f'Step {i}')
    # Process observation and return Action + Ref Dicts
    action, ref_dict, rand2ref = observe_and_act(observation, ref_dict, rand2ref, action_history)
    # Perform action on environment
    observation, reward, terminated, truncated, info = env.step(action)

    print(reward, terminated)

    # Episode is over
    if terminated:
        if reward > 0:
            # todo: save successful episode:
            # dom, actions, refs, ref_dict to transform doms and actions
            # rewards etc
            continue
        break

    time.sleep(0.15)

Step 0
screenshot shape: (210, 160, 3)
t5_input: Click button ONE.<body ref=4 width=1200.0 height=210.0 bg_color=rgb(0.33, 0.33, 0.33) fg_color=rgb(0.0, 0.0, 0.0)><div ref=3 width=160.0 height=210.0 id=wrap bg_color=rgb(1.0, 1.0, 1.0) fg_color=rgb(0.0, 0.0, 0.0)><div ref=5 top=50.0 width=160.0 height=4.0 id=area bg_color=rgb(0.0, 0.0, 0.0) fg_color=rgb(0.0, 0.0, 0.0)><button ref=2 left=86.0 top=136.0 width=40.0 height=40.0 text=ONE id=subbtn bg_color=rgb(0.94, 0.94, 0.94) fg_color=rgb(0.0, 0.0, 0.0)></button><button ref=1 left=109.0 top=68.0 width=40.0 height=40.0 text=TWO id=subbtn2 bg_color=rgb(0.94, 0.94, 0.94) fg_color=rgb(0.0, 0.0, 0.0)></button></div></div></body>
about to make request: {'instruction_input': 'Click button ONE.<body ref=4 width=1200.0 height=210.0 bg_color=rgb(0.33, 0.33, 0.33) fg_color=rgb(0.0, 0.0, 0.0)><div ref=3 width=160.0 height=210.0 id=wrap bg_color=rgb(1.0, 1.0, 1.0) fg_color=rgb(0.0, 0.0, 0.0)><div ref=5 top=50.0 width=160.0 height=4.0 id=area bg_color=r

-1.0 True
